In [0]:
%pip install pdf2image pytesseract Pillow


Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
%pip install PyMuPDF


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 23.5/23.5 MB 34.3 MB/s eta 0:00:00
Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
import fitz  # PyMuPDF
import pytesseract
from PIL import Image
import io

pdf_path = "/Volumes/workspace/invoice/invoice_data/batch1-0001.pdf"

doc = fitz.open(pdf_path)

full_text = ""

for page_index in range(len(doc)):
    page = doc.load_page(page_index)

    # Extract images from the page
    images = page.get_images(full=True)
    
    for img_index, img in enumerate(images):
        xref = img[0]
        base_image = doc.extract_image(xref)
        image_bytes = base_image["image"]

        # Load into PIL
        pil_img = Image.open(io.BytesIO(image_bytes))

        # OCR
        text = pytesseract.image_to_string(pil_img)
        full_text += text + "\n"

print(full_text)


Invoice no: 51109338

Date of issue: 04/13/2013

Seller: Client:

Andrews, Kirby and Valdez Becker Ltd

58861 Gonzalez Prairie 8012 Stewart Summit Apt. 455
Lake Daniellefurt, IN 57228 North Douglas, AZ 95355

Tax Id: 945-82-2137 Tax Id: 942-80-0517

IBAN: GB75MCRL06841367619257

ITEMS
No. Description Qty UM Net price Net worth VAT [%] Gross
worth
1. CLEARANCE! Fast Dell Desktop 3,00 each 209,00 627,00 10% 689,70
Computer PC DUAL CORE
WINDOWS 10 4/8/16GB RAM
2. HP T520 Thin Client Computer 5,00 each 37,75 188,75 10% 207,63
AMD GX-212JC 1.2GHz 4GB RAM
TESTED !!READ BELOW!!
3: gaming pc desktop computer 1,00 each 400,00 400,00 10% 440,00
4. 12-Core Gaming Computer 3,00 each 464,89 1 394,67 10% 1 534,14
Desktop PC Tower Affordable
GAMING PC 8GB AMD Vega RGB
5) Custom Build Dell Optiplex 9020 5,00 each 221,99 1 109,95 10% 1 220,95
MT i5-4570 3.20GHz Desktop
Computer PC
6. Dell Optiplex 990 MT Computer 4,00 each 269,95 1 079,80 10% 1 187,78
PC Quad Core i7 3.4GHz 16GB
2TB HD Windows 10 Pro
U

In [0]:
import fitz   # PyMuPDF
import pytesseract
from PIL import Image
import io
import os
from pyspark.sql import Row
import shutil

# ---------------------------
# Folder structure inside Volume
# ---------------------------
input_path = "/Volumes/workspace/invoice/input/"
processed_path = "/Volumes/workspace/invoice/processed/"

# Ensure processed folder exists
os.makedirs(processed_path, exist_ok=True)

rows = []

# ---------------------------
# LOOP OVER INPUT PDF FILES
# ---------------------------
for file in os.listdir(input_path):

    if not file.lower().endswith(".pdf"):
        continue

    pdf_path = os.path.join(input_path, file)
    print(f"Processing PDF: {pdf_path}")

    doc = fitz.open(pdf_path)
    ocr_text = ""

    # ---------------------------
    # OCR EACH PAGE
    # ---------------------------
    for page_index in range(len(doc)):
        page = doc.load_page(page_index)
        images = page.get_images(full=True)

        for img in images:
            xref = img[0]
            base = doc.extract_image(xref)
            img_bytes = base["image"]

            pil_img = Image.open(io.BytesIO(img_bytes))

            text = pytesseract.image_to_string(pil_img)
            ocr_text += text + "\n"

    # Append into Bronze rows
    rows.append(Row(
        filename=file,
        raw_text=ocr_text
    ))

    # ---------------------------
    # MOVE FILE → processed/
    # ---------------------------
    src = pdf_path
    dst = os.path.join(processed_path, file)

    print(f"Moving file to processed folder: {dst}")
    shutil.move(src, dst)

print("All files processed and moved.\n")

# ---------------------------
# CREATE BRONZE TABLE
# ---------------------------
bronze_df = spark.createDataFrame(rows)

bronze_df.write.mode("overwrite").format("delta").saveAsTable(
    "workspace.invoice.bronze_invoices_multi"
)

display(bronze_df)


Processing PDF: /Volumes/workspace/invoice/input/batch1-0001.pdf
Moving file to processed folder: /Volumes/workspace/invoice/processed/batch1-0001.pdf
Processing PDF: /Volumes/workspace/invoice/input/batch1-0002.pdf
Moving file to processed folder: /Volumes/workspace/invoice/processed/batch1-0002.pdf
Processing PDF: /Volumes/workspace/invoice/input/batch1-0003.pdf
Moving file to processed folder: /Volumes/workspace/invoice/processed/batch1-0003.pdf
Processing PDF: /Volumes/workspace/invoice/input/batch1-0004.pdf
Moving file to processed folder: /Volumes/workspace/invoice/processed/batch1-0004.pdf
Processing PDF: /Volumes/workspace/invoice/input/batch1-0005.pdf
Moving file to processed folder: /Volumes/workspace/invoice/processed/batch1-0005.pdf
Processing PDF: /Volumes/workspace/invoice/input/batch1-0006.pdf
Moving file to processed folder: /Volumes/workspace/invoice/processed/batch1-0006.pdf
Processing PDF: /Volumes/workspace/invoice/input/batch1-0007.pdf
Moving file to processed fold

filename raw_text batch1-0001.pdf Invoice no: 51109338

Date of issue: 04/13/2013

Seller: Client:

Andrews, Kirby and Valdez Becker Ltd

58861 Gonzalez Prairie 8012 Stewart Summit Apt. 455
Lake Daniellefurt, IN 57228 North Douglas, AZ 95355

Tax Id: 945-82-2137 Tax Id: 942-80-0517

IBAN: GB75MCRL06841367619257

ITEMS
No. Description Qty UM Net price Net worth VAT [%] Gross
worth
1. CLEARANCE! Fast Dell Desktop 3,00 each 209,00 627,00 10% 689,70
Computer PC DUAL CORE
WINDOWS 10 4/8/16GB RAM
2. HP T520 Thin Client Computer 5,00 each 37,75 188,75 10% 207,63
AMD GX-212JC 1.2GHz 4GB RAM
TESTED !!READ BELOW!!
3: gaming pc desktop computer 1,00 each 400,00 400,00 10% 440,00
4. 12-Core Gaming Computer 3,00 each 464,89 1 394,67 10% 1 534,14
Desktop PC Tower Affordable
GAMING PC 8GB AMD Vega RGB
5) Custom Build Dell Optiplex 9020 5,00 each 221,99 1 109,95 10% 1 220,95
MT i5-4570 3.20GHz Desktop
Computer PC
6. Dell Optiplex 990 MT Computer 4,00 each 269,95 1 079,80 10% 1 187,78
PC Quad Core i7 3.4GHz 16GB
2TB HD Windows 10 Pro
Us Dell Core 2 Duo Desktop 5,00 each 168,00 840,00 10% 924,00
Computer | Windows XP Pro |
4GB | 500GB
SUMMARY
VAT [%] Net worth VAT Gross worth
10% 5 640,17 564,02 6 204,19

Total $ 5 640,17 $ 564,02 $ 6 204,19

 batch1-0002.pdf Invoice no: 12847181

Date of issue:

Seller:

Fitzpatrick and Sons
00480 Cook Cove
Spencerport, UT 12036

Tax Id: 998-99-5253
IBAN: GB92PBPQ73499358975916

ITEMS
No. Description Qty
1. HP Desktop Computer PC J] 4,00

Core i5 16GB 2TB HD 256GB
SSD 22" LCD J Windows 10

2. CUSTOM BUILT AMD RYZEN 3,00
THREADRIPPER GAMING
COMPUTER , 32 GB RAM,

3: Fast Dell Optiplex Desktop PC 1,00
Computer Dual Core 3.4Ghz
8GB 1TB Win 10 Pro WIFI

4. Dell Optiplex 790 Computer i7 3,00
@ 3.40 Ghz Quad Core 250GB
4GB Working

a Vintage Microsolutions Pentium 2,00

133mhz Desktop Tower PC
Windows 95 5.25 Floppy

SUMMARY

VAT [%]
10%

Total

03/03/2012

UM

eac

eac

eac

eac

h

n

eac

Client:
Duncan PLC

Unit 8799 Box 0703

DPO AP 81970

Tax Id: 911-82-7132

Net price

139,95

1 400,00

217,00

159,99

390,00

Net worth
6 236,77

$ 6 236,77

Net worth

559,80

4 200,00

217,00

479,97

780,00

VAT [%]

10%

10%

10%

10%

10%

VAT

623,68

$ 623,68

Gross
worth

615,78

4 620,00

238,70

527,97

858,00

Gross worth

6 860,45

$ 6 860,45

 batch1-0003.pdf Invoice no: 19471831

Date of issue:

Seller:

Palmer Ltd
9790 Bauer Hills Apt. 146
South Patriciaton, SD 32497

Tax Id: 924-71-1106
IBAN: GBO5YUTG50853913677557

ITEMS

No. Description

1. 15"x15" White Decorative
Coffee Table Top Lapis Lazuli
Marquetery Patio Décor

2. 4'x2' Marble Dining Table Top
Pietra Dura Birds Inlay Art
Furniture Decors B444

3: 60 Inches Marble Dinning Table

Top Hand Inlaid Garden Table
with Gemstones

SUMMARY

Total

04/09/2014

Qty uM
3,00 each
5,00 each
5,00 each

VAT [%]

10%

Client:

Net price

645,77

1 840,10

5 908,00

Net worth
40 677,81

$ 40 677,81

Rios, Oneill and Rowe
3571 Tina Trafficway
Buckleyland, LA 97688

Tax Id: 922-72-5979

Net worth VAT [%]

1937/31; 10%
9 200,50 10%
29 540,00 10%

VAT

4 067,78

$ 4 067,78

Gross
worth

2 131,04

10 120,55

32 494,00

Gross worth
44 745,59

$ 44 745,59

 batch1-0004.pdf Invoice no: 16273983

Date of issue:

Seller:

Reyes, Holloway and Lee
38676 Johnson Burg Suite 666
West Rebeccamouth, SD 02588

Tax Id: 909-83-7738
IBAN: GB96VWUL52026848004193

ITEMS
No. Description Qty
al Handmade Thick round warm 4,00

crochet Rug Carpet Mat 97%
acrylic 3% me Floor Decor

2. Rug White Moroccan Beni 2,00
Ourain Trellis Shag Area Rug
Authentic Handmade Carpet

3: Abstract Living Room Carpet 1,00
Home Decor Nordic Style
Bedside Area Rug Floor Mats

4. Leopard Printed Rug Skin Mat 1,00
Leather Faux Fur Animals Area
Rugs Home Carpets

S: 1pc Exquisite Durable Foot 2,00

Cloth Christmas Carpet Xmas
Cushion for Kitchen

SUMMARY

VAT [%]
10%

Total

04/01/2017

UM

eacn

eacn

eacn

eacn

eacn

Client:
Castillo LLC

70391 Kelsey Terrace
Garcialand, VT 41740

Tax Id: 901-88-0463

Net price

44,99
